In [1]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
import plotly.io as pio
pio.templates.default="plotly_white"

# Field calculations
See [HPS Chicane Current Setting](https://misportal.jlab.org/mis/physics/hps_notes/viewFile.cfm/2015-007.pdf?documentId=10) and also [Confluence page](https://confluence.slac.stanford.edu/display/hpsg/Beamline+and+Magnet)

## Summary:
The relation between the beam energy and the central value of the field is:
$$B_0 = A\cdot E_b$$ 
Where $A = 0.22727\ \mathrm{Tesla/GeV}$ was found emperically during the test run.

The current to field relationship is found from the measured excitation curve of the magnet as:
$$I = a\cdot B_0 + b $$
Where $a = 0.1537 \cdot 10^4\ \mathrm{A/T}$ and $b = 0.6657\ \mathrm{A}$.

## Creating a new fieldmap.

Get the original text based measured fieldmaps. Eg BmapCorrected3D_8k.txt for the 8k Gauss field. Then unfold and scale this field with the java command:
<code>
   java $HPSJAVA org.hps.util.UnfoldFieldmap <fieldmap> <scaling factor>
</code>


In [2]:
A = 0.22727
a = 0.1537E4
b = 0.6657
#
# Beam energy for experiment.
# 
Eb = 3.742
# Eb = 1.92
# Eb = 4.556651
B0 = A*Eb
I = a * B0 + b
print(f"For beam energy {Eb:6.3f} GeV,  B0 = {B0:7.4f} T  and I = {I:7.2f} A")

For beam energy  3.742 GeV,  B0 =  0.8504 T  and I = 1307.80 A


In [3]:
# field_map_k_value = 4
field_map_k_value = 8
base_field_map = pd.read_csv("/data/HPS/compute_fieldmaps/BmapCorrected3D_"+str(field_map_k_value)+"k.txt",sep="\s+", header=None, index_col=None)
print(base_field_map.iloc[0:2])
ratio_denum = base_field_map.iloc[0, 4]/10000 # Gauss to T: 1 T = 10000 Gauss
print(f"Denumerator for field scaling with this file = {ratio_denum}")

     0    1    2             3        4             5
0  0.0  0.0  0.0 -2.622320e-14  8009.62 -1.684030e-09
1  0.0  0.0  0.5 -2.622320e-14  8009.62 -1.684030e-09
Denumerator for field scaling with this file = 0.800962


In [5]:
#
# Actual measured current used by experiment.
#
I_m = 1322 # 679
B0_m = (I_m - b)/a
print(f"The measured current of {I_m:7.2f} A gives B0 = {B0_m:7.4} T")
print(f"Ratio to the 8k fieldmap: {B0_m/0.801:8.9f}")
print(f"Ratio to the "+str(field_map_k_value)+f"k fieldmap: {B0_m/ratio_denum:8.9f}")

The measured current of 1322.00 A gives B0 =  0.8597 T
Ratio to the 8k fieldmap: 1.073263414
Ratio to the 8k fieldmap: 1.073314333


In [10]:
#
# Magnetic field map that is used by hps-java
#
# 2021 run
#dat0 = pd.read_csv("/data/HPS/fieldmap/334acm3_8kg_corrected_unfolded_scaled_1.0508.dat",delim_whitespace=True, skiprows=9,names=['X','Y','Z','BX','BY','BZ'])
dat = pd.read_csv("/data/HPS/fieldmap/334acm3_8kg_corrected_unfolded_scaled_1.07326.dat",delim_whitespace=True, skiprows=9,names=['X','Y','Z','BX','BY','BZ'])
#dat = pd.read_csv("/data/HPS/fieldmap/334acm3_8kg_corrected_unfolded_scaled_1.0.dat",delim_whitespace=True, skiprows=9,names=['X','Y','Z','BX','BY','BZ'])
# 2019 run
#dat = pd.read_csv("/data/HPS/fieldmap/418acm2_10kg_corrected_unfolded_scaled_1.0319.dat",delim_whitespace=True, skiprows=9,names=['X','Y','Z','BX','BY','BZ'])
B_min = np.min(dat.BY)
B_max_abs = 1000*np.max(np.abs(dat.BY))
bmax_z=dat.Z[dat.BY == B_min]
bmax_y=dat.Y[dat.BY == B_min]
bmax_x=dat.X[dat.BY == B_min]
max_field_points = [ (bmax_x.iloc[i],bmax_y.iloc[i],bmax_z.iloc[i]) for i in range(len(bmax_x))]
print(f"Max field strength in BY: {B_max_abs:8.5f} T")
# print("Locations of Max field strength: ",end="")
# for fp in max_field_points:
#     print(fp,end = ",")
# print("\n")
center_point = (dat.X == 0) & (dat.Y == 0) & (dat.Z == 0)
B_center = -1000*(dat.BY[center_point].values[0])
print(f"Desired central value based on current: {B0_m:9.7f}")
print(f"Central value of B_y     : {B_center:8.6f} T")
print(f"Ratio to calculated field: {B_center/B0_m:8.6f}  Error = {100*(B_center - B0_m)/B0_m:7.3f}% ")
center_point_hps_java = (dat.X == 0) & (dat.Y == 0) & (dat.Z == 5)
B_hps_java = -1000*(dat.BY[center_point_hps_java].values[0])
print(f"Value used by hps-java   : {B_hps_java:8.6f} T")
print(f"Ratio to calculated field: {B_hps_java/B0_m:8.6f}  Error = {100*(B_hps_java - B0_m)/B0_m:7.3f}% ")

Max field strength in BY:  0.87350 T
Desired central value based on current: 0.8596840
Central value of B_y     : 0.859600 T
Ratio to calculated field: 0.999902  Error =  -0.010% 
Value used by hps-java   : 0.859600 T
Ratio to calculated field: 0.999902  Error =  -0.010% 


In [11]:
center_line = (dat.X == 0) & (dat.Y == 0)
fig = go.Figure(
    data = [
        go.Scatter(x=dat.Z[center_line], y= 1000*dat.BY[center_line], name="center line")
    ]
)
fig.update_layout(
    title=go.layout.Title(
        text="HPS Magnetic field 2021 Run",
        yanchor="top",
        y=0.86,
        xanchor="center",
        x=0.5,
        font=dict(size=18)),
    xaxis=go.layout.XAxis(
        title=go.layout.xaxis.Title(text="$Z\ [mm]$"),
        tickfont=dict(size=14),
        titlefont=dict(size=16)
    ),
    yaxis=go.layout.YAxis(
        title=go.layout.yaxis.Title(
            text="$B_y\ [T]$"),
        tickfont=dict(size=14),
        titlefont=dict(size=16)
    )
)
fig.show()

In [12]:
center_plane = (dat.Y == 0)
fig = go.Figure(
    data = [
        go.Contour(x=dat.Z[center_plane], y= dat.X[center_plane], z = 1000*dat.BY[center_plane], 
                   contours_coloring='heatmap',
                   name="center line")
    ]
)
fig.update_layout(
    title=go.layout.Title(
        text="HPS Magnetic field 2021 Run",
        yanchor="top",
        y=0.86,
        xanchor="center",
        x=0.5,
        font=dict(size=18)),
    xaxis=go.layout.XAxis(
        title=go.layout.xaxis.Title(text="$Z\ [mm]$"),
        tickfont=dict(size=14),
        titlefont=dict(size=16),
        range=[-900,900]
    ),
    yaxis=go.layout.YAxis(
        title=go.layout.yaxis.Title(
            text="$X\ [mm]$"),
        tickfont=dict(size=14),
        titlefont=dict(size=16)
    )
)
fig.show()